In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
%matplotlib inline

# Constants

In [69]:
available_proteins = {
    "P01137": dict(Protein="Transforming growth factor beta-1 proprotein", Gene="TGFB1", Species="HUMAN", UniAcc="P01137", URL_desc="https://alphafold.ebi.ac.uk/entry/P01137"),
    "P04202": dict(Protein="Transforming growth factor beta-1 proprotein", Gene="Tgfb1", Species="MOUSE", UniAcc="P04202", URL_desc="https://alphafold.ebi.ac.uk/entry/P04202"),
    "P04075": dict(Protein="Fructose-bisphosphate aldolase A", Gene="ALDOA", Species="HUMAN", UniAcc="P04075", URL_desc="https://alphafold.ebi.ac.uk/entry/P04075"),
    "P05064": dict(Protein="Fructose-bisphosphate aldolase A", Gene="Aldoa", Species="MOUSE", UniAcc="P05064", URL_desc="https://alphafold.ebi.ac.uk/entry/P05064"),
    "P09651": dict(Protein="Heterogeneous nuclear ribonucleoprotein A1", Gene="HNRNPA1", Species="HUMAN", UniAcc="P09651", URL_desc="https://alphafold.ebi.ac.uk/entry/P09651"),
    "P49312": dict(Protein="Heterogeneous nuclear ribonucleoprotein A1", Gene="Hnrnpa1", Species="MOUSE", UniAcc="P49312", URL_desc="https://alphafold.ebi.ac.uk/entry/P49312")
}
available_proteins = pd.DataFrame(available_proteins)
available_proteins = available_proteins.transpose()
available_proteins

Protein     Gene Species  UniAcc  \
P01137  Transforming growth factor beta-1 proprotein    TGFB1   HUMAN  P01137   
P04202  Transforming growth factor beta-1 proprotein    Tgfb1   MOUSE  P04202   
P04075              Fructose-bisphosphate aldolase A    ALDOA   HUMAN  P04075   
P05064              Fructose-bisphosphate aldolase A    Aldoa   MOUSE  P05064   
P09651    Heterogeneous nuclear ribonucleoprotein A1  HNRNPA1   HUMAN  P09651   
P49312    Heterogeneous nuclear ribonucleoprotein A1  Hnrnpa1   MOUSE  P49312   

                                        URL_desc  
P01137  https://alphafold.ebi.ac.uk/entry/P01137  
P04202  https://alphafold.ebi.ac.uk/entry/P04202  
P04075  https://alphafold.ebi.ac.uk/entry/P04075  
P05064  https://alphafold.ebi.ac.uk/entry/P05064  
P09651  https://alphafold.ebi.ac.uk/entry/P09651  
P49312  https://alphafold.ebi.ac.uk/entry/P49312

In [35]:
essential_aminoacids = [
    {"code": "A", "name": "Alanine"},
    {"code": "R", "name": "Arginine"},
    {"code": "N", "name": "Asparagine"},
    {"code": "D", "name": "Aspartic acid"},
    {"code": "C", "name": "Cysteine"},
    {"code": "Q", "name": "Glutamine"},
    {"code": "E", "name": "Glutamic acid"},
    {"code": "G", "name": "Glycine"},
    {"code": "H", "name": "Histidine"},
    {"code": "I", "name": "Isoleucine"},
    {"code": "L", "name": "Leucine"},
    {"code": "K", "name": "Lysine"},
    {"code": "M", "name": "Methionine"},
    {"code": "F", "name": "Phenylalanine"},
    {"code": "P", "name": "Proline"},
    {"code": "S", "name": "Serine"},
    {"code": "T", "name": "Threonine"},
    {"code": "W", "name": "Tryptophan"},
    {"code": "Y", "name": "Tyrosine"},
    {"code": "V", "name": "Valine"},
    {"code": "O", "name": "Pyrrolysine"},
    {"code": "U", "name": "Selenocysteine"},
    {"code": "B", "name": "Aspartic acid or Asparagine"},
    {"code": "Z", "name": "Glutamic acid or Glutamine"},
    {"code": "X", "name": "Any amino acid"},
    {"code": "J", "name": "Leucine or Isoleucine"}
]
essential_aminoacids = pd.DataFrame(essential_aminoacids)
essential_aminoacids.head()

code           name
0    A        Alanine
1    R       Arginine
2    N     Asparagine
3    D  Aspartic acid
4    C       Cysteine

In [3]:
cat_cm = px.colors.qualitative.Dark24

# Functions

In [4]:
def get_structure(df, uniacc,  index=None):
    out = df.loc[df["UniAcc"] == uniacc, :].reset_index()
    if index is not None:
        out.set_index(index)
    else:
        out.reset_index()
    return out

# Loading, creating and preprocessing datasets

In [7]:
df_structures_raw = pd.read_csv("../data/BioVis-challenge-alphafold-data.csv")
df_modifications_raw = pd.read_csv("../data/BioVis-challenge-test-data.csv")

In [10]:
print(df_structures_raw.columns)
df_structures_raw.head()

Index(['UniAcc', 'RES', 'POS', 'quality', 'x_coord_c', 'x_coord_ca',
       'x_coord_cb', 'x_coord_n', 'y_coord_c', 'y_coord_ca', 'y_coord_cb',
       'y_coord_n', 'z_coord_c', 'z_coord_ca', 'z_coord_cb', 'z_coord_n',
       'secondary_structure', 'structure_group', 'BEND', 'HELX', 'STRN',
       'TURN', 'unstructured'],
      dtype='object')


UniAcc RES  POS  quality  x_coord_c  x_coord_ca  x_coord_cb  x_coord_n  \
0  P01137   M    1    34.62      8.477       8.149       9.266      7.911   
1  P01137   P    2    43.64      6.612       7.968       8.455      7.952   
2  P01137   P    3    44.84      4.721       5.419       5.943      6.601   
3  P01137   S    4    45.81      2.571       2.474       1.049      3.392   
4  P01137   G    5    42.28      3.279       3.839         NaN      3.525   

   y_coord_c  y_coord_ca  ...  z_coord_ca  z_coord_cb  z_coord_n  \
0    -23.762     -22.378  ...      96.955      96.058     98.116   
1    -24.913     -25.130  ...      95.490      95.388     96.927   
2    -25.663     -24.420  ...      92.676      91.582     93.453   
3    -26.758     -26.627  ...      91.576      92.009     92.096   
4    -28.985     -27.727  ...      88.132         NaN     89.558   

   secondary_structure  structure_group  BEND HELX STRN  TURN  unstructured  
0         unstructured     unstructured     0    0    0     0             1  
1         unstructured     unstructured     0    0    0     0             1  
2         unstructured     unstructured     0    0    0     0             1  
3         unstructured     unstructured     0    0    0     0             1  
4         unstructured     unstructured     0    0    0     0             1  

[5 rows x 23 columns]

In [72]:
# processing structures
df_structures = df_structures_raw.copy()

if 0 not in df_structures["POS"].unique():
    df_structures["POS"] = df_structures["POS"] - 1 # 0 indexing
    
df_structures["dist_ca_c"] = np.sqrt(np.sum(np.square(df_structures.loc[:, ["x_coord_ca", "y_coord_ca", "z_coord_ca"]].values - df_structures.loc[:, ["x_coord_c", "y_coord_c", "z_coord_c"]].values), axis=1))
df_structures["dist_ca_cb"] = np.sqrt(np.sum(np.square(df_structures.loc[:, ["x_coord_ca", "y_coord_ca", "z_coord_ca"]].values - df_structures.loc[:, ["x_coord_cb", "y_coord_cb", "z_coord_cb"]].values), axis=1))
df_structures["dist_ca_n"] = np.sqrt(np.sum(np.square(df_structures.loc[:, ["x_coord_ca", "y_coord_ca", "z_coord_ca"]].values - df_structures.loc[:, ["x_coord_n", "y_coord_n", "z_coord_n"]].values), axis=1))
    
df_structures.head()    

UniAcc RES  POS  quality  x_coord_c  x_coord_ca  x_coord_cb  x_coord_n  \
0  P01137   M    0    34.62      8.477       8.149       9.266      7.911   
1  P01137   P    1    43.64      6.612       7.968       8.455      7.952   
2  P01137   P    2    44.84      4.721       5.419       5.943      6.601   
3  P01137   S    3    45.81      2.571       2.474       1.049      3.392   
4  P01137   G    4    42.28      3.279       3.839         NaN      3.525   

   y_coord_c  y_coord_ca  ...  secondary_structure  structure_group  BEND  \
0    -23.762     -22.378  ...         unstructured     unstructured     0   
1    -24.913     -25.130  ...         unstructured     unstructured     0   
2    -25.663     -24.420  ...         unstructured     unstructured     0   
3    -26.758     -26.627  ...         unstructured     unstructured     0   
4    -28.985     -27.727  ...         unstructured     unstructured     0   

   HELX  STRN  TURN unstructured dist_ca_c  dist_ca_cb  dist_ca_n  
0     0     0     0            1  1.524252    1.535973   1.483317  
1     0     0     0            1  1.540917    1.530158   1.462604  
2     0     0     0            1  1.535302    1.529109   1.454803  
3     0     0     0            1  1.538659    1.538291   1.463325  
4     0     0     0            1  1.534436         NaN   1.470492  

[5 rows x 26 columns]

In [24]:
df_modifications_raw.head()

UniAcc RES  POS                 MOD        Entry   Gene Species  \
0  P04075   M    1  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
1  P04075   Y    3  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
2  P04075   Y    5  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
3  P04075   E   11  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
4  P04075   K   13  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   

        classification  PathogenicMutation  
0  Chemical derivative               False  
1             Artefact               False  
2             Artefact               False  
3             Artefact               False  
4             Artefact               False

In [173]:
# processing modifications
df_modifications = df_modifications_raw.copy()

if 0 not in df_modifications["POS"].unique():
    df_modifications["POS"] = df_modifications["POS"] - 1 # 0 indexing
    
df_modifications.head()

UniAcc RES  POS                 MOD        Entry   Gene Species  \
0  P04075   M    0  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
1  P04075   Y    2  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
2  P04075   Y    4  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
3  P04075   E   10  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
4  P04075   K   12  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   

        classification  PathogenicMutation  
0  Chemical derivative               False  
1             Artefact               False  
2             Artefact               False  
3             Artefact               False  
4             Artefact               False

# Combining and saving datasets

In [33]:
df_modifications.classification.unique()

array(['Chemical derivative', 'Artefact', nan, 'Post-translational',
       'Pre-translational', 'Multiple', 'Other glycosylation',
       'O-linked glycosylation', 'N-linked glycosylation',
       'Co-translational', 'glyco'], dtype=object)

In [62]:
tmp = df_modifications.groupby(["UniAcc", "POS", "RES"]).agg(
    num_mods_total=("PathogenicMutation", "count"),
    num_mods_pathogenic=("PathogenicMutation", lambda g: g.sum()),
    num_mods_nonpathogenic=("PathogenicMutation", lambda g: len(g) - g.sum()),
    num_class_Chemical_derivative= ('classification', lambda g: (g==str("Chemical derivative")).sum()),
    num_class_Artefact= ('classification', lambda g: (g==str("Artefact")).sum()),
    num_class_nan= ('classification', lambda g: (g==str(np.nan)).sum()),
    num_class_Post_translational= ('classification', lambda g: (g==str("Post-translational")).sum()),
    num_class_Pre_translational= ('classification', lambda g: (g==str("Pre-translational")).sum()),
    num_class_Multiple= ('classification', lambda g: (g==str("Multiple")).sum()),
    num_class_Other_glycosylation= ('classification', lambda g: (g==str("Other glycosylation")).sum()),
    num_class_O_linked_glycosylation= ('classification', lambda g: (g==str("O-linked glycosylation")).sum()),
    num_class_N_linked_glycosylation= ('classification', lambda g: (g==str("N-linked glycosylation")).sum()),
    num_class_Co_translational= ('classification', lambda g: (g==str("Co-translational")).sum()),
    num_class_glyco= ('classification', lambda g: (g==str("glyco")).sum())
#    **{str(k).replace(" ", "_"): ("classification", lambda g: temp_fn(k, g)) for k in df_modifications.classification.unique()}
)
tmp = tmp.reset_index()
tmp.head()

UniAcc  POS RES  num_mods_total  num_mods_pathogenic  \
0  P01137   44   R               1                    1   
1  P01137   57   R               1                    0   
2  P01137   59   A               2                    0   
3  P01137   61   P               1                    0   
4  P01137   62   P               1                    0   

   num_mods_nonpathogenic  num_class_Chemical_derivative  num_class_Artefact  \
0                       0                              0                   1   
1                       1                              0                   1   
2                       2                              1                   0   
3                       1                              1                   0   
4                       1                              1                   0   

   num_class_nan  num_class_Post_translational  num_class_Pre_translational  \
0              0                             0                            0   
1              0                             0                            0   
2              0                             1                            0   
3              0                             0                            0   
4              0                             0                            0   

   num_class_Multiple  num_class_Other_glycosylation  \
0                   0                              0   
1                   0                              0   
2                   0                              0   
3                   0                              0   
4                   0                              0   

   num_class_O_linked_glycosylation  num_class_N_linked_glycosylation  \
0                                 0                                 0   
1                                 0                                 0   
2                                 0                                 0   
3                                 0                                 0   
4                                 0                                 0   

   num_class_Co_translational  num_class_glyco  
0                           0                0  
1                           0                0  
2                           0                0  
3                           0                0  
4                           0                0

In [73]:
# merging datasets
if "num_mods_total" not in df_structures.columns:
    df_structures = df_structures.merge(tmp, how="left", left_on=["UniAcc", "POS", "RES"], right_on=["UniAcc", "POS", "RES"])
    df_structures = df_structures.fillna(0.0)
if "RES_name" not in df_structures.columns and "code" not in df_structures.columns:
    df_structures = df_structures.merge(essential_aminoacids, how="left", left_on=["RES"], right_on="code")
    df_structures = df_structures.drop("code", axis=1)
    df_structures = df_structures.rename(columns={"name": "RES_name"})
if "Species" not in df_structures.columns:
    df_structures = df_structures.merge(available_proteins, how="left", left_on=["UniAcc"], right_on="UniAcc")

df_structures["has_mods"] = df_structures.num_mods_total > 0
df_structures.head()

UniAcc RES  POS  quality  x_coord_c  x_coord_ca  x_coord_cb  x_coord_n  \
0  P01137   M    0    34.62      8.477       8.149       9.266      7.911   
1  P01137   P    1    43.64      6.612       7.968       8.455      7.952   
2  P01137   P    2    44.84      4.721       5.419       5.943      6.601   
3  P01137   S    3    45.81      2.571       2.474       1.049      3.392   
4  P01137   G    4    42.28      3.279       3.839       0.000      3.525   

   y_coord_c  y_coord_ca  ...  num_class_O_linked_glycosylation  \
0    -23.762     -22.378  ...                               0.0   
1    -24.913     -25.130  ...                               0.0   
2    -25.663     -24.420  ...                               0.0   
3    -26.758     -26.627  ...                               0.0   
4    -28.985     -27.727  ...                               0.0   

   num_class_N_linked_glycosylation  num_class_Co_translational  \
0                               0.0                         0.0   
1                               0.0                         0.0   
2                               0.0                         0.0   
3                               0.0                         0.0   
4                               0.0                         0.0   

   num_class_glyco    RES_name                                       Protein  \
0              0.0  Methionine  Transforming growth factor beta-1 proprotein   
1              0.0     Proline  Transforming growth factor beta-1 proprotein   
2              0.0     Proline  Transforming growth factor beta-1 proprotein   
3              0.0      Serine  Transforming growth factor beta-1 proprotein   
4              0.0     Glycine  Transforming growth factor beta-1 proprotein   

    Gene Species                                  URL_desc  has_mods  
0  TGFB1   HUMAN  https://alphafold.ebi.ac.uk/entry/P01137     False  
1  TGFB1   HUMAN  https://alphafold.ebi.ac.uk/entry/P01137     False  
2  TGFB1   HUMAN  https://alphafold.ebi.ac.uk/entry/P01137     False  
3  TGFB1   HUMAN  https://alphafold.ebi.ac.uk/entry/P01137     False  
4  TGFB1   HUMAN  https://alphafold.ebi.ac.uk/entry/P01137     False  

[5 rows x 46 columns]

In [74]:
# Check that all the modifications were accounted for
len(df_modifications) == df_structures.loc[df_structures.has_mods, :].num_mods_total.sum()

True

In [175]:
# general information
if "RES_name" not in df_modifications.columns and "code" not in df_modifications.columns:
    df_modifications = df_modifications.merge(essential_aminoacids, how="left", left_on=["RES"], right_on="code")
    df_modifications = df_modifications.drop("code", axis=1)
    df_modifications = df_modifications.rename(columns={"name": "RES_name"})
df_modifications.head()

UniAcc RES  POS                 MOD        Entry   Gene Species  \
0  P04075   M    0  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
1  P04075   Y    2  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
2  P04075   Y    4  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
3  P04075   E   10  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   
4  P04075   K   12  [4]Carbamidomethyl  ALDOA_HUMAN  ALDOA   HUMAN   

        classification  PathogenicMutation       RES_name  
0  Chemical derivative               False     Methionine  
1             Artefact               False       Tyrosine  
2             Artefact               False       Tyrosine  
3             Artefact               False  Glutamic acid  
4             Artefact               False         Lysine

In [136]:
# creating neighbors datasets 
dfs = []
for acc in df_structures.UniAcc.unique():
    df_view = df_structures.loc[df_structures.UniAcc == acc, :].reset_index()
    out = []
    for _, item_x in df_view.iterrows():        
        for _, item_y in df_view.iterrows():
            tmp = dict(UniAcc=acc, POS_x=item_x.POS, POS_y=item_y.POS)
            dif_vec = item_x[["x_coord_ca", "y_coord_ca", "z_coord_ca"]] - item_y[["x_coord_ca", "y_coord_ca", "z_coord_ca"]]            
            tmp["distance_ca"] = np.sqrt(np.sum(np.square(dif_vec)))
            if item_x.POS - 1 == item_y.POS or item_x.POS + 1 == item_y.POS:
                tmp["are_neighbors"] = 1
            else:
                tmp["are_neighbors"] = 0
            out.append(tmp)
    dfs.append(out)

In [139]:
len(df_neighbors)

809976

In [138]:
df_neighbors = pd.concat([pd.DataFrame(d) for d in dfs], axis=0)

In [141]:
df_neighbors.head(10)

UniAcc  POS_x  POS_y  distance_ca  are_neighbors
0  P01137      0      0     0.000000              0
1  P01137      0      1     3.122898              1
2  P01137      0      2     5.471061              0
3  P01137      0      3     8.899060              0
4  P01137      0      4    11.181826              0
5  P01137      0      5    14.355127              0
6  P01137      0      6    16.603218              0
7  P01137      0      7    18.126599              0
8  P01137      0      8    20.357228              0
9  P01137      0      9    22.736938              0

In [169]:
df_nearest_neighbors = df_neighbors.sort_values("distance_ca").groupby(["UniAcc", "POS_x"]).head(30).sort_values(["UniAcc", "POS_x", "distance_ca"])

In [176]:
# write datasets to disk
df_structures.to_json("/Users/chadepl/Downloads/df_structures.json", orient="records")
df_modifications.to_json("/Users/chadepl/Downloads/df_modifications.json", orient="records")
df_neighbors.to_json("/Users/chadepl/Downloads/df_neighbors.json", orient="records")
df_nearest_neighbors.to_json("/Users/chadepl/Downloads/df_nearest_neighbors.json", orient="records")

# Exploratory analysis

## Protein structures (structures)

In [32]:

# New columns

df_structures["structured"] = 1 - df_structures["unstructured"]

df_structures = df_structures.join(available_proteins, on="UniAcc", rsuffix="r")

print("Shape: [{}, {}]".format(len(df_structures), len(df_structures.columns)))
print("Columns: {}".format(df_structures.columns))

Shape: [2200, 29]
Columns: Index(['UniAcc', 'RES', 'POS', 'quality', 'x_coord_c', 'x_coord_ca',
       'x_coord_cb', 'x_coord_n', 'y_coord_c', 'y_coord_ca', 'y_coord_cb',
       'y_coord_n', 'z_coord_c', 'z_coord_ca', 'z_coord_cb', 'z_coord_n',
       'secondary_structure', 'structure_group', 'BEND', 'HELX', 'STRN',
       'TURN', 'unstructured', 'structured', 'protein', 'gene', 'organism',
       'UniAccr', 'alphafold_link'],
      dtype='object')


### Why are there different types of x, y, z coordinates?

In [65]:
structure = available_proteins.iloc[5]
df_structure = get_structure(df_structures, structure.UniAcc, "POS")
coord_type = ["c", "ca", "cb", "n"][0]

In [66]:
# Plot alpha carbons trace

fig = px.scatter_3d(df_structure, x="x_coord_ca", y ="y_coord_ca", z ="z_coord_ca")
fig.update_traces(mode="lines+markers", marker=dict(size=4), line=dict(width=2, color="black"))

trace_groups = {
    "c": dict(edges_x=[], edges_y=[], edges_z=[], color="blue"),
    "cb": dict(edges_x=[], edges_y=[], edges_z=[], color="green"),
    "n": dict(edges_x=[], edges_y=[], edges_z=[], color="orange")
}

for i in range(len(df_structure)):
    for atom, color in zip(["c", "cb", "n"], ["blue", "green", "orange"]):
        p1 = df_structure.loc[i, ["x_coord_ca", "y_coord_ca", "z_coord_ca"]].values
        p2 = df_structure.loc[i, ["x_coord_{}".format(atom), "y_coord_{}".format(atom), "z_coord_{}".format(atom)]].values
        trace_groups[atom]["edges_x"].append(p1[0])
        trace_groups[atom]["edges_x"].append(p2[0])
        trace_groups[atom]["edges_x"].append(None)
        trace_groups[atom]["edges_y"].append(p1[1])
        trace_groups[atom]["edges_y"].append(p2[1])
        trace_groups[atom]["edges_y"].append(None)
        trace_groups[atom]["edges_z"].append(p1[2])
        trace_groups[atom]["edges_z"].append(p2[2])
        trace_groups[atom]["edges_z"].append(None)

for k, v in trace_groups.items():
    fig.add_trace(go.Scatter3d(x=v["edges_x"], 
                               y=v["edges_y"], 
                               z=v["edges_z"], 
                               marker_color=v["color"], 
                               marker_size=2, line_width=1, name=k))

fig.update_layout(margin=dict(l=0, r=0, b=0, t=0), showlegend=True)
fig.update_scenes(xaxis_visible=False, yaxis_visible=False, zaxis_visible=False)

fig.show()

### What does the field unstructured mean?

In [8]:
totals = df_structures.sum(axis=0)[["BEND", "HELX", "STRN", "TURN", "unstructured"]]
print(totals)
print("{}/{}".format(totals.sum(),len(df_structures)))

BEND            149
HELX            719
STRN            460
TURN            194
unstructured    678
dtype: object
2200/2200


In [9]:
print(df_structures.structure_group.unique())
print(df_structures.secondary_structure.unique())

['unstructured' 'BEND' 'TURN' 'HELX' 'STRN']
['unstructured' 'BEND' 'TURN_TY1_P' 'HELX_RH_AL_P' 'HELX_LH_PP_P'
 'HELX_RH_3T_P' 'STRN']


In [10]:
fig = px.scatter(df_structures, 
                    x="x_coord_ca", y="y_coord_ca", #z="z_coord_ca", 
                    color="unstructured",
                 color_continuous_scale = px.colors.colorbrewer.Set1,
                   facet_col="UniAcc", facet_col_wrap=2)
fig.update_traces(marker_size=3, line_width=1, mode="markers")
#fig.update_layout(height=300)
fig.show()

### Are structures the same across species?

In [11]:
available_proteins.join(df_structures.groupby("UniAcc").count().loc[:, ["POS"]], on="UniAcc")

protein     gene organism  \
P01137  Transforming growth factor beta-1 proprotein    TGFB1    HUMAN   
P04202  Transforming growth factor beta-1 proprotein    Tgfb1    MOUSE   
P04075              Fructose-bisphosphate aldolase A    ALDOA    HUMAN   
P05064              Fructose-bisphosphate aldolase A    Aldoa    MOUSE   
P09651    Heterogeneous nuclear ribonucleoprotein A1  HNRNPA1    HUMAN   
P49312    Heterogeneous nuclear ribonucleoprotein A1  Hnrnpa1    MOUSE   

        UniAcc                            alphafold_link  POS  
P01137  P01137  https://alphafold.ebi.ac.uk/entry/P01137  390  
P04202  P04202  https://alphafold.ebi.ac.uk/entry/P04202  390  
P04075  P04075  https://alphafold.ebi.ac.uk/entry/P04075  364  
P05064  P05064  https://alphafold.ebi.ac.uk/entry/P05064  364  
P09651  P09651  https://alphafold.ebi.ac.uk/entry/P09651  372  
P49312  P49312  https://alphafold.ebi.ac.uk/entry/P49312  320

In [12]:
prot_human = get_structure(df_structures, "P09651")
prot_mouse = get_structure(df_structures, "P49312")

marker_config = dict(size=2)

fig = go.Figure(data=[
    go.Scatter3d(x=prot_human.x_coord_ca, y=prot_human.y_coord_ca, z=prot_human.z_coord_ca, marker=marker_config, name="HUMAM"),
    go.Scatter3d(x=prot_mouse.x_coord_ca, y=prot_mouse.y_coord_ca, z=prot_mouse.z_coord_ca, marker=marker_config, name="MOUSE")
])
fig.update_layout(margin=dict(t=0,b=0,l=0,r=0))
fig.show()

### What is the distribution of distances between adjacent residues?

In [14]:
res_coords = df_structures.loc[:, ["UniAcc", "POS", "x_coord_ca", "y_coord_ca", "z_coord_ca"]]#.values

In [23]:
dfs = []
for acc in res_coords.UniAcc.unique():
    tmp = res_coords.loc[res_coords.UniAcc==acc, ["x_coord_ca", "y_coord_ca", "z_coord_ca"]]
    res_dists = np.sqrt(np.sum(np.square(tmp.values[:-1] - tmp.values[1:]), axis=1))
    tmp_df = pd.DataFrame({"UniAcc": acc, "dists": res_dists})
    dfs.append(tmp_df)
res_dists = pd.concat(dfs)

In [163]:
res_dists = np.sqrt(np.sum(np.square(res_coords[:-1] - res_coords[1:]), axis=1))

In [25]:
fig = px.histogram(res_dists, x="dists", nbins=100, title="Distribution of distances between adjacent residues")
#fig.update_traces(customdata=np.arange(len(res_dists)), hovertemplate="<b>%{customdata}</b>")
fig.show()

In [153]:
from sklearn.neighbors import NearestNeighbors

In [218]:
nn = NearestNeighbors(n_neighbors=res_coords.shape[0], algorithm="brute").fit(res_coords)
distances, indices = nn.kneighbors(res_coords)

In [220]:
fig = px.histogram(distances[:,1:].flatten())
fig.show()

In [222]:
fig = go.Figure() #px.histogram(x=distances[:,3], nbins=100)

for i in range(1, 20):
    fig.add_trace(go.Histogram(x=distances[:,i], nbinsx=1000))
    
fig.update_layout(barmode="overlay")
fig.update_traces(opacity=1)

fig.show()

In [214]:
distances[0:5, 0:5]

array([[ 0.        ,  3.12289769,  5.47106068,  8.89905989, 11.18182588],
       [ 0.        ,  3.12289769,  3.86265414,  6.90973523,  8.82797904],
       [ 0.        ,  3.84107719,  3.86265414,  5.47106068,  5.83785791],
       [ 0.        ,  3.84107719,  3.8645001 ,  6.02774137,  6.90973523],
       [ 0.        ,  3.8645001 ,  3.88301339,  5.83785791,  6.26438353]])

In [215]:
indices[0:5, 0:5]

array([[0, 1, 2, 3, 4],
       [1, 0, 2, 3, 4],
       [2, 3, 1, 0, 4],
       [3, 2, 4, 5, 1],
       [4, 3, 5, 2, 6]])

In [91]:
print(structure.x_coord_ca[0:5])
print(structure.x_coord_ca[1:5])
len(structure.x_coord_ca[1:])

0    8.149
1    7.968
2    5.419
3    2.474
4    3.839
Name: x_coord_ca, dtype: float64
1    7.968
2    5.419
3    2.474
4    3.839
Name: x_coord_ca, dtype: float64


389

### Which parts of the proteins' structure prediction have higher quality?

In [ ]:
marker_config_ca = dict(color=cat_cm[1], size=(100-structure["quality"])*0.5)
marker_config_rest = dict(color="rgb(0,0,0)", size=1)
line_config_1 = dict(width=2)
line_config_2 = dict(width=0)
t_ca = go.Scatter3d(x = structure["x_coord_ca"], y = structure["y_coord_ca"], z = structure["z_coord_ca"], marker = marker_config_ca, line=line_config_1)
marker_config_rest["color"] = cat_cm[1]
t_cb = go.Scatter3d(x = structure["x_coord_cb"], y = structure["y_coord_cb"], z = structure["z_coord_cb"], marker = marker_config_rest, line=line_config_2)
marker_config_rest["color"] = cat_cm[2]
t_c = go.Scatter3d(x = structure["x_coord_c"], y = structure["y_coord_c"], z = structure["z_coord_c"], marker = marker_config_rest, line=line_config_2)
marker_config_rest["color"] = cat_cm[3]
t_n = go.Scatter3d(x = structure["x_coord_n"], y = structure["y_coord_n"], z = structure["z_coord_n"], marker = marker_config_rest, line=line_config_2)
layout = go.Layout()#xaxis=dict(visible=False), yaxis=dict(visible=False), zaxis=dict(visible=False))
fig = go.Figure(data=[t_ca, t_cb, t_c, t_n], layout=layout)
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))
fig.show()

In [273]:
df_structures.columns

Index(['UniAcc', 'RES', 'POS', 'quality', 'x_coord_c', 'x_coord_ca',
       'x_coord_cb', 'x_coord_n', 'y_coord_c', 'y_coord_ca', 'y_coord_cb',
       'y_coord_n', 'z_coord_c', 'z_coord_ca', 'z_coord_cb', 'z_coord_n',
       'secondary_structure', 'structure_group', 'BEND', 'HELX', 'STRN',
       'TURN', 'unstructured', 'protein', 'gene', 'organism', 'UniAccr',
       'alphafold_link', 'proteinr', 'gener', 'organismr', 'UniAccr',
       'alphafold_linkr'],
      dtype='object')

In [281]:
fig = px.histogram(df_structures, x="quality", color="UniAcc")
fig.show()

protein           Transforming growth factor beta-1 proprotein
gene                                                     TGFB1
organism                                                 HUMAN
UniAcc                                                  P01137
alphafold_link        https://alphafold.ebi.ac.uk/entry/P01137
Name: P01137, dtype: object

In [306]:
structure = available_proteins.iloc[5]
df_structure = get_structure(df_structures, structure.UniAcc)
fig = px.scatter_3d(df_structure, 
                    x="x_coord_ca", 
                    y="y_coord_ca", 
                    z="z_coord_ca",
                    title="{}-{} ({})".format(structure.UniAcc, structure.protein, structure.organism),
                    size=100-df_structure["quality"], 
                    color=df_structure["quality"])
fig.update_traces(mode="lines+markers", line_color=df_structure["quality"])
#fig.update_layout(margin=dict(t=10,r=0,b=0,l=0))
fig.show()

## Post translational modifications (modifications)

In [30]:
if 0 not in df_modifications["POS"].unique():
    df_modifications["POS"] = df_modifications["POS"] - 1 # 0 indexing
    
print("Shape: [{}, {}]".format(len(df_modifications), len(df_modifications.columns)))
print("Columns: {}".format(df_modifications.columns))


Shape: [6880, 9]
Columns: Index(['UniAcc', 'RES', 'POS', 'MOD', 'Entry', 'Gene', 'Species',
       'classification', 'PathogenicMutation'],
      dtype='object')


In [29]:
structure = available_proteins.iloc[2]
#df_tmp = df_modifications
df_mod_group = get_structure(df_modifications, structure["UniAcc"])
df_mod_group = df_mod_group.groupby("MOD").agg(num_mods=("UniAcc","count"), 
                                   exists_pathogenic=("PathogenicMutation", np.any), 
                                   num_pathogenic = ("PathogenicMutation", lambda g: len(g[g == True])),
                                   fraction_pathogenic=("PathogenicMutation", lambda g: len(g[g == True])/len(g[g == False])),
                                   ).reset_index()

df_mod_group.head()

Shape: [2200, 29]
Columns: Index(['UniAcc', 'RES', 'POS', 'quality', 'x_coord_c', 'x_coord_ca',
       'x_coord_cb', 'x_coord_n', 'y_coord_c', 'y_coord_ca', 'y_coord_cb',
       'y_coord_n', 'z_coord_c', 'z_coord_ca', 'z_coord_cb', 'z_coord_n',
       'secondary_structure', 'structure_group', 'BEND', 'HELX', 'STRN',
       'TURN', 'unstructured', 'structured', 'protein', 'gene', 'organism',
       'UniAccr', 'alphafold_link'],
      dtype='object')


MOD  num_mods  exists_pathogenic  num_pathogenic  \
0         [1009]Thiazolidine        30              False               0   
1          [1014]glycidamide         7              False               0   
2                 [1017]DMPO         1              False               0   
3  [1031]Biotin:Thermo-88310        11              False               0   
4        [1032]2-nitrobenzyl         1              False               0   

   fraction_pathogenic  
0                  0.0  
1                  0.0  
2                  0.0  
3                  0.0  
4                  0.0

In [571]:
colors = ["red" if i else "blue" for i in df_mod_group.exists_pathogenic.values]
fig = go.Figure(data=[go.Bar(x=df_mod_group.MOD.values, 
                             y=df_mod_group.num_mods.values,
                             marker_color=colors,
                            orientation="v")])
fig.update_traces(customdata=df_mod_group.loc[:, ["num_pathogenic", "num_mods"]],
                  hovertemplate="%{customdata[0]}/%{customdata[1]} are pathogenic]")
fig.update_layout(title="Modifications in {}-{}({})".format(structure.UniAcc, structure.protein, structure.organism),
                 xaxis_tickmode="linear")
fig.show()

In [565]:
df_tmp = get_structure(df_modifications, structure["UniAcc"]).reset_index()

mods_labels = df_tmp.MOD.unique()
fig_data = []
for res in df_tmp.RES.unique():
    df_trace = df_tmp[df_tmp.RES == res].groupby(["MOD"]).agg(num_mods=("UniAcc", "count")).reset_index()
    fig_data.append(go.Bar(name=res, x=df_trace.MOD, y=df_trace.num_mods))

fig = go.Figure(data = fig_data)
fig.update_layout(barmode="stack", xaxis_tickmode="linear")
fig.show()

In [566]:
df_res_group = get_structure(df_modifications, structure["UniAcc"])
df_res_group = df_res_group.groupby("RES").agg(num_mods=("UniAcc","count"), 
                                   exists_pathogenic=("PathogenicMutation", np.any), 
                                   num_pathogenic = ("PathogenicMutation", lambda g: len(g[g == True])),
                                   fraction_pathogenic=("PathogenicMutation", lambda g: len(g[g == True])/len(g[g == False])),
                                   ).reset_index()
df_res_group.head()

RES  num_mods  exists_pathogenic  num_pathogenic  fraction_pathogenic
0   A         2              False               0                0.000
1   C        18               True               2                0.125
2   D         3              False               0                0.000
3   E        11               True               1                0.100
4   F         4              False               0                0.000

In [568]:
colors = ["red" if i else "blue" for i in df_res_group.exists_pathogenic.values]
fig = go.Figure(data=[go.Bar(x=df_res_group.RES.values, 
                             y=df_res_group.num_mods.values,
                             marker_color=colors,
                            orientation="v")])
fig.update_traces(customdata=df_res_group.loc[:, ["num_pathogenic", "num_mods"]],
                  hovertemplate="%{customdata[0]}/%{customdata[1]} are pathogenic]")
fig.update_layout(title="Modifications in {}-{}({})".format(structure.UniAcc, structure.protein, structure.organism),
                 xaxis_tickmode="linear")
fig.show()

In [569]:
df_tmp = get_structure(df_modifications, structure["UniAcc"]).reset_index()

res_labels = df_tmp.RES.unique()
fig_data = []
for mod in df_tmp.MOD.unique():
    df_trace = df_tmp[df_tmp.MOD == mod].groupby(["RES"]).agg(num_res=("UniAcc", "count")).reset_index()
    fig_data.append(go.Bar(name=mod, x=df_trace.RES, y=df_trace.num_res))

fig = go.Figure(data = fig_data)
fig.update_layout(barmode="stack", xaxis_tickmode="linear")
fig.show()

## Structures meet modifications
This is the result of performing an inner join between `df_structures` and `df_modifications` based on the UniAcc and POS fields. The join is performed at this point in the notebook to include all the computed fields and processing steps of the base datasets.

`df_modifications` already contains most of the information we need. Nevertheless, for analysis, an additional piece of information that df_structures contains is the location of the different atoms. 

In [450]:
structure = available_proteins.iloc[4]
df_str = get_structure(df_structures, structure.UniAcc).reset_index()
df_mod = get_structure(df_modifications, structure.UniAcc).reset_index()
df_plot = df_str.copy()

df_num_mods = df_mod.groupby("POS").count()["UniAcc"].reset_index()
df_num_mods = df_num_mods.rename(columns={"UniAcc": "num_mods"})

df_exists_pathogenic = df_mod.groupby(["POS"]).any().loc[:, ["PathogenicMutation"]].reset_index()
df_exists_pathogenic = df_exists_pathogenic.rename(columns={"PathogenicMutation": "exists_pathogenic"})

df_plot = df_plot.merge(df_num_mods, how="left", left_on="POS", right_on="POS")
df_plot = df_plot.fillna(value={"num_mods": 0})

df_plot = df_plot.merge(df_exists_pathogenic, how="left", left_on="POS", right_on="POS")
df_plot = df_plot.fillna(value={"exists_pathogenic": False})

max_size = 20
min_size = 0
max_data_size = df_plot.num_mods.values.max()
min_data_size = df_plot.num_mods.values.min()
sizes = ((df_plot.num_mods - min_data_size)/(max_data_size - min_data_size))*(max_size - min_size) + min_size

fig = px.scatter_3d(df_plot, 
                    x="x_coord_ca", 
                    y="y_coord_ca", 
                    z="z_coord_ca",
                   title="{}-{} ({}) | pathogenic: {}".format(structure.UniAcc, structure.protein, structure.organism, len(df_exists_pathogenic[df_exists_pathogenic["exists_pathogenic"] == True])))
fig.update_traces(mode="lines", line_color="gray", hoverinfo="none", hovertemplate=None)

fig.add_trace(go.Scatter3d(
    x=df_plot["x_coord_ca"], 
    y=df_plot["y_coord_ca"], 
    z=df_plot["z_coord_ca"], 
    marker_size=sizes,
    marker_color=df_plot["exists_pathogenic"].apply(lambda a: "red" if a else "blue"),
    customdata=df_plot.num_mods.values,
    hovertemplate = "<b>%{customdata}</b>",
    mode="markers"))
fig.update_traces()

fig.update_layout(showlegend=True)

fig.update_scenes(xaxis_visible=False, yaxis_visible=False, zaxis_visible=False)
fig.show()

## New dataset: neighborhoods

This will allow us to see patterns of recurrence.

In [445]:
df_plot.num_mods.values

array([ 2.,  0.,  6.,  0.,  0.,  0.,  2., 13.,  5.,  1.,  4.,  3.,  0.,
        7., 23.,  4.,  6.,  4.,  2.,  2.,  3., 14.,  5., 15., 10.,  6.,
        8.,  7.,  8.,  1., 13.,  4.,  3.,  1.,  8.,  5., 14.,  3., 10.,
        3., 24., 20., 36.,  3.,  2., 10., 15.,  9.,  1.,  1.,  2.,  5.,
        1.,  0., 23.,  0.,  3.,  0.,  7.,  3., 19., 16.,  4., 10.,  2.,
       16., 12.,  1.,  8.,  1.,  2., 10.,  6.,  2.,  7.,  2.,  7., 10.,
        0.,  1.,  0.,  1.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        2.,  0.,  0.,  0.,  3.,  1.,  0.,  0.,  0.,  1.,  0.,  2.,  0.,
        9.,  3.,  0.,  0.,  0.,  0.,  0.,  0., 10.,  3.,  1.,  0.,  4.,
        4.,  4.,  3.,  1.,  6.,  4.,  2.,  2.,  2.,  1.,  2.,  0., 13.,
        0.,  1.,  0.,  1.,  4.,  4.,  9.,  4.,  4.,  5.,  0.,  2.,  0.,
        7.,  6., 14.,  1.,  2.,  1.,  4.,  1., 16.,  3., 19., 13., 13.,
       10., 11.,  0.,  7., 14.,  0.,  0.,  0.,  3., 17.,  7.,  2.,  2.,
        3.,  5.,  0.,  2.,  4., 19.,  6.,  0.,  3.,  3.,  0.,  0